# 1. Basic Notation

## 1.1 Graph Representation

- Let the set of nodes (junctions) be $\mathcal{N}$, with n=$|\mathcal{N}|$
- Let the set of branches (pipes, pumps, valves etc.) be $\mathcal{E}$, with $e=|\mathcal{E}|$

Each branch $e\in\mathcal{E}$ connects two nodes. We define a direction (orientation) for each branch. This orientation can be chosen arbitrarily as long as it is kept consistent throughout the equations (it does not have to match actual flow direction in practice; it’s just a bookkeeping device).

## 1.2 Incidence Matrix

Define the incidence matrix $A\in\mathbb{R}^{n\times e}$ by:

$$
A_{i,j} = 
\begin{cases}
+1 & \text{if branch }j\text{ enters node } i, \\
-1 & \text{if branch }j\text{ leaves node } i, \\
0  & \text{otherwise.}
\end{cases}
$$

## 1.3 Variables

- **Nodal pressures**: Let $p_i$ denote the pressure at node $i$. Collect these as a vector:

$$
\vec{p} =
\begin{bmatrix}
p_1 \\
p_2 \\
\vdots \\
p_n
\end{bmatrix}
$$

Often, one node is chosen as a reference (ground) with $p_\text{ref}=0$, reducing the number of unknown pressures. E.g., a node exposed to atmosphere.

- **Branch flowrates**: Let $q_j$ denote the volumetric flowrate (or mass flowrate as per the decided convention) in branch $j$. Collect these as a vector:
$$
\vec{q} =
\begin{bmatrix}
q_1 \\
q_2 \\
\vdots \\
q_e
\end{bmatrix}
$$

A positive $q_j$ means a positive flow in the direction of the branch $j$; negative $q_j$ means a flow in the opposite direction.

- **Branch pressure change**: Let $\Delta p_j$ denote the pressure change in the direction of the branch $j$. By definition,

$$\Delta p_j = p_\text{node at "outlet" of j} - p_\text{node at "inlet" of j}$$

Collect these as a vector:

$$
\vec{\Delta p} =
\begin{bmatrix}
\Delta p_1 \\
\Delta p_2\\
\vdots \\
\Delta p_e
\end{bmatrix}
$$

Note that there is a standard relationship between the nodal pressure vector, $\vec{p}$ and $\vec{\Delta p}$ via the mapping incidence matrix $A$. We can then relate these via:

$$\vec{\Delta p}=A^\top\vec{p}$$

if the convention of $A_{i,j}=+1$ when branch $j$ ends at node $i$ and -1 when is starts at node $i$ (as above).


# 2. Steady-State Formulation

## 2.1 Mass (or Volume) Balance at Each Node (KCL)

In steady state, there is no accumulation at each node, so the net flow into each node is zero (assuming constant fluid density if using volume for branch flow):

$$A\vec{q}=0$$

This is a direct analog of Kirchoff's Current Law (KCL) in circuit theory.

## 2.2 Pressure-Flow Relationships in Each Branch

For each branch $j$, there is a contituitive relation between flow, $q_j$, and pressure drop $\Delta p_j$. For example:

- **(Linear) Hydraulic Resistance** (e.g., laminar flow major losses in a pipe): Analogous to ohms law in circuits, becomes more complex (and nonlinear) for turbulent losses, controlled valve pressure drops/ cv curves etc.

$$\Delta p_j = R_j q_j$$

- **Pump or "voltage source"**: May either be a fixed $\Delta p_j = \text{constant}$ or a more complex pump curve $\Delta p_j = f(q_j)$.

In general we have a nonlinear relationship of the form:

$$\vec{\Delta p} = \mathbf{f}(\vec{q})$$

For a purely linear system, we simply have:

$\vec{\Delta p} = R\vec{q}$ where $R$ is a matrix of resistances.

## 2.3 Assembling the Steady-State System

We then have a system of equations:

1. $\vec{\Delta p} = A^\top \vec{p}$ (pressure differences from nodal pressures)
2. $\vec{\Delta p} = f(\vec{q})$ (branch constitutive laws)
3. $A \vec{q} = 0$ (mass continuity)

Generalised in matrix form:

$$
\begin{bmatrix}
    A& 0 \\
    0 & A^\top
\end{bmatrix}
\begin{bmatrix}
    \vec{q} \\
    \vec{p}
\end{bmatrix}
-\begin{bmatrix}
    0 \\
    \mathbf{f}(\vec{q})
\end{bmatrix}
= 0
$$

$$
\begin{bmatrix}
    -q_1 + q_4 + q_5 \\
    q_1 - q_2 \\
    q_2 - q_3 \\
    q_3 - q_4 - q_5 \\
    p_2 - \rho g h_1 \\
    -p_2 + p_3 - f_\text{pump}(q_2) \\
    -p_3 + p_4 - f_\text{pipe}(q_3) + \rho gh_1 \\
    -p_4 - f_\text{fcv1}(q_4) \\
    -p_4 - f_\text{fcv2}(q_5) \\
\end{bmatrix}
= 0
$$

In [8]:
"""PARAMETERS"""

DENSITY = 880.0  # kg/m^3
G = 9.81  # m/s^2
FRICTION_FACTOR = 0.02
PIPE_LENGTH = 10.0  # m
PIPE_DIAMETER = 0.1  # m
STATIC_HEAD = DENSITY * G * 10.0
NUM_OF_PUMPS = 2

In [9]:
"""NETWORK GEOMETRY"""

import numpy as np


N_NODES = 4
N_BRANCHES = 5

INTERFACE_MATRIX = np.zeros((N_NODES, N_BRANCHES))
INTERFACE_MATRIX[0, 0] = -1
INTERFACE_MATRIX[1, 0] = 1
INTERFACE_MATRIX[1, 1] = -1
INTERFACE_MATRIX[2, 1] = 1
INTERFACE_MATRIX[2, 2] = -1
INTERFACE_MATRIX[3, 2] = 1
INTERFACE_MATRIX[0, 3] = 1
INTERFACE_MATRIX[3, 3] = -1
INTERFACE_MATRIX[0, 4] = 1
INTERFACE_MATRIX[3, 4] = -1

In [10]:
"""NONLINEAR TERMS"""

from utils import darcy_weisbach_pressure_drop, valve_pressure_drop, pump_pressure_rise


def pump_source_dp(q, pump_speed, num_of_pumps, density, g):
    return pump_pressure_rise(q / num_of_pumps, pump_speed, density, g)


def valve_1_loss_dp(q, valve_position, density, g):
    return valve_pressure_drop(q, valve_position, density, g)


def valve_2_loss_dp(q, valve_position, density, g):
    return valve_pressure_drop(q, valve_position, density, g)


def pipe_loss_dp(q, friction_factor, pipe_length, pipe_diameter, density):
    return darcy_weisbach_pressure_drop(
        q, friction_factor, pipe_length, pipe_diameter, density
    )


def calculate_delta_pressures(q, u):
    pump_speed, valve_1_position, valve_2_position = u
    return np.array(
        [
            STATIC_HEAD,
            pump_source_dp(q[1], pump_speed, NUM_OF_PUMPS, DENSITY, G),
            -pipe_loss_dp(q[2], FRICTION_FACTOR, PIPE_LENGTH, PIPE_DIAMETER, DENSITY)
            - STATIC_HEAD,
            -valve_1_loss_dp(q[3], valve_1_position, DENSITY, G),
            -valve_2_loss_dp(q[4], valve_2_position, DENSITY, G),
        ]
    )

In [11]:
"""STEADY STATE RHS"""


def rhs(z, u, scaling_factor):
    x = z * scaling_factor
    q = x[:N_BRANCHES]
    p = x[N_BRANCHES:]
    q = np.maximum(q, 0)
    p[0] = 0.0

    return np.concatenate(
        [
            INTERFACE_MATRIX @ q,
            INTERFACE_MATRIX.T @ p - calculate_delta_pressures(q, u),
        ]
    )

In [12]:
"""STEADY STATE SOLVER"""

from scipy.optimize import fsolve


def solve_steady_state(u):
    q0 = np.array([0.3] * N_BRANCHES)
    p0 = np.array([1e5] * N_NODES)
    p0[0] = 0.0
    scaling_factor = np.concatenate([q0, p0])
    z0 = np.ones(N_BRANCHES + N_NODES)
    sol = fsolve(
        rhs,
        z0,
        args=(
            u,
            scaling_factor,
        ),
        xtol=1e-10,
        maxfev=int(1e8),
        full_output=True,
    )
    return sol[0] * scaling_factor, sol[1], sol[2]  # x, infodict, ier

In [ ]:
"""STEADY-STATE SIMULATION"""

import pandas as pd
import plotly.express as px
from tqdm import tqdm

pump_speeds = np.linspace(0.1, 1, 20)
valve_1_positions = np.linspace(0.2, 1, 20)
valve_2_positions = np.linspace(0.2, 1, 20)
pump_speeds, valve_1_positions, valve_2_positions = np.meshgrid(
    pump_speeds, valve_1_positions, valve_2_positions
)
pump_speeds = pump_speeds.flatten()
valve_1_positions = valve_1_positions.flatten()
valve_2_positions = valve_2_positions.flatten()

df = pd.DataFrame(
    {
        "pump_speed": pump_speeds,
        "valve_1_position": valve_1_positions,
        "valve_2_position": valve_2_positions,
    }
)


for index, row in tqdm(df.iterrows(), total=len(df)):
    pump_speed = row["pump_speed"]
    valve_1_position = row["valve_1_position"]
    valve_2_position = row["valve_2_position"]

    q0 = np.array([0.3] * N_BRANCHES)
    p0 = np.array([1e5] * N_NODES)
    p0[0] = 0.0

    z0 = np.ones(N_BRANCHES + N_NODES)

    func_pump_source = lambda q: pump_pressure_rise(q, pump_speed, DENSITY, G)
    func_valve_1_loss = lambda q: valve_pressure_drop(q, valve_1_position, DENSITY, G)
    func_valve_2_loss = lambda q: valve_pressure_drop(q, valve_2_position, DENSITY, G)
    func_pipe_loss = lambda q: darcy_weisbach_pressure_drop(
        q, FRICTION_FACTOR, PIPE_LENGTH, PIPE_DIAMETER, DENSITY
    )

    sol = solve_steady_state([pump_speed, valve_1_position, valve_2_position])
    for i, q in enumerate(sol[0][:N_BRANCHES] * q0):
        df.loc[index, f"q{i+1}"] = q

    for i, p in enumerate(sol[0][N_BRANCHES:] * p0):
        df.loc[index, f"p{i+1}"] = p
    df.loc[index, "sol.result"] = sol[2]


df = df[
    (
        (df["sol.result"] == 1)
        & (df["q1"] > 0)
        & (df["q2"] > 0)
        & (df["q3"] > 0)
        & (df["q4"] > 0)
        & (df["q5"] > 0)
        & (df["p1"] > -1e3)
        & (df["p2"] > -1e3)
        & (df["p3"] > -1e3)
        & (df["p4"] > -1e3)
    )
]

df["Pump Speed (%)"] = df["pump_speed"] * 100
df["Valve 1 Position (%)"] = df["valve_1_position"] * 100
df["Valve 2 Position (%)"] = df["valve_2_position"] * 100
df["q1 (l/s)"] = df["q1"] * 1000
df["q2 (l/s)"] = df["q2"] * 1000
df["q3 (l/s)"] = df["q3"] * 1000
df["q4 (l/s)"] = df["q4"] * 1000
df["q5 (l/s)"] = df["q5"] * 1000
df["p1 (barg)"] = df["p1"] / 1e5
df["p2 (barg)"] = df["p2"] / 1e5
df["p3 (barg)"] = df["p3"] / 1e5
df["p4 (barg)"] = df["p4"] / 1e5

# df.to_csv("output\\Simplified Parallel Example.csv", index=False)

fig = px.scatter_3d(
    df[df["Valve 2 Position (%)"] == df["Valve 2 Position (%)"].iloc[-1]],
    x="Pump Speed (%)",
    y="Valve 1 Position (%)",
    z="q1 (l/s)",
    color="q1 (l/s)",
)
fig.update_layout(scene=dict(aspectmode="cube"))
fig.update_layout(
    template="plotly_dark",
    paper_bgcolor="#1f1f1f",
    margin=dict(t=50, b=0, l=0, r=0),
    height=800,
)

In [ ]:
df_saved = pd.read_csv("output\\Simplified Parallel Example.csv")

fig = px.scatter_3d(
    df_saved.iloc[::10],
    x="Pump Speed (%)",
    y="Valve 1 Position (%)",
    z="q1 (l/s)",
    color="Valve 2 Position (%)",
)
fig.update_traces(marker=dict(size=1))
fig.update_layout(scene=dict(aspectmode="cube"), template="plotly_dark", paper_bgcolor="#1f1f1f", margin=dict(t=50, b=0, l=0, r=0), height=800)